# Sentiment Analysis with an RNN

In this notebook, you'll implement a recurrent neural network that performs sentiment analysis. 
>Using an RNN rather than a strictly feedforward network is more accurate since we can include information about the *sequence* of words. 

Here we'll use a dataset of movie reviews, accompanied by sentiment labels: positive or negative.

<img src="assets/reviews_ex.png" width=40%>

### Network Architecture

The architecture for this network is shown below.

<img src="assets/network_diagram.png" width=40%>

>**First, we'll pass in words to an embedding layer.** We need an embedding layer because we have tens of thousands of words, so we'll need a more efficient representation for our input data than one-hot encoded vectors. You should have seen this before from the Word2Vec lesson. You can actually train an embedding with the Skip-gram Word2Vec model and use those embeddings as input, here. However, it's good enough to just have an embedding layer and let the network learn a different embedding table on its own. *In this case, the embedding layer is for dimensionality reduction, rather than for learning semantic representations.*

>**After input words are passed to an embedding layer, the new embeddings will be passed to LSTM cells.** The LSTM cells will add *recurrent* connections to the network and give us the ability to include information about the *sequence* of words in the movie review data. 

>**Finally, the LSTM outputs will go to a sigmoid output layer.** We're using a sigmoid function because positive and negative = 1 and 0, respectively, and a sigmoid will output predicted, sentiment values between 0-1. 

We don't care about the sigmoid outputs except for the **very last one**; we can ignore the rest. We'll calculate the loss by comparing the output at the last time step and the training label (pos or neg).

---
### Load in and visualize the data

In [29]:
import numpy as np

# read data from text files
with open('data/reviews.txt', 'r') as f:
    reviews = f.read()
with open('data/labels.txt', 'r') as f:
    labels = f.read()

In [30]:
print(reviews[:2000])
print()
print(labels[:20])

bromwell high is a cartoon comedy . it ran at the same time as some other programs about school life  such as  teachers  . my   years in the teaching profession lead me to believe that bromwell high  s satire is much closer to reality than is  teachers  . the scramble to survive financially  the insightful students who can see right through their pathetic teachers  pomp  the pettiness of the whole situation  all remind me of the schools i knew and their students . when i saw the episode in which a student repeatedly tried to burn down the school  i immediately recalled . . . . . . . . . at . . . . . . . . . . high . a classic line inspector i  m here to sack one of your teachers . student welcome to bromwell high . i expect that many adults of my age think that bromwell high is far fetched . what a pity that it isn  t   
story of a man who has unnatural feelings for a pig . starts out with a opening scene that is a terrific example of absurd comedy . a formal orchestra audience is turn

## Data pre-processing

The first step when building a neural network model is getting your data into the proper form to feed into the network. Since we're using embedding layers, we'll need to encode each word with an integer. We'll also want to clean it up a bit.

You can see an example of the reviews data above. Here are the processing steps, we'll want to take:
>* We'll want to get rid of periods and extraneous punctuation.
* Also, you might notice that the reviews are delimited with newline characters `\n`. To deal with those, I'm going to split the text into each review using `\n` as the delimiter. 
* Then I can combined all the reviews back together into one big string.

First, let's remove all punctuation. Then get all the text without the newlines and split it into individual words.

In [31]:
from string import punctuation

print(punctuation)

# get rid of punctuation
reviews = reviews.lower() # lowercase, standardize
all_text = ''.join([c for c in reviews if c not in punctuation])

!"#$%&'()*+,-./:;<=>?@[\]^_`{|}~


In [32]:
# split by new lines and spaces
reviews_split = all_text.split('\n')
all_text = ' '.join(reviews_split)

# create a list of words
words = all_text.split()

In [33]:
words[:30]

['bromwell',
 'high',
 'is',
 'a',
 'cartoon',
 'comedy',
 'it',
 'ran',
 'at',
 'the',
 'same',
 'time',
 'as',
 'some',
 'other',
 'programs',
 'about',
 'school',
 'life',
 'such',
 'as',
 'teachers',
 'my',
 'years',
 'in',
 'the',
 'teaching',
 'profession',
 'lead',
 'me']

### Encoding the words

The embedding lookup requires that we pass in integers to our network. The easiest way to do this is to create dictionaries that map the words in the vocabulary to integers. Then we can convert each of our reviews into integers so they can be passed into the network.

> **Exercise:** Now you're going to encode the words with integers. Build a dictionary that maps words to integers. Later we're going to pad our input vectors with zeros, so make sure the integers **start at 1, not 0**.
> Also, convert the reviews to integers and store the reviews in a new list called `reviews_ints`. 

In [17]:
# feel free to use this import 
from collections import Counter

## Build a dictionary that maps words to integers
counts = Counter(words)
vocab = sorted(counts, key=counts.get, reverse=True)
vocab_to_int = {word: ii for ii, word in enumerate(vocab, 1)}

## use the dict to tokenize each review in reviews_split
## store the tokenized reviews in reviews_ints
reviews_ints = []
for review in reviews_split:
    reviews_ints.append([vocab_to_int[word] for word in review.split()])



In [18]:
words

['bromwell',
 'high',
 'is',
 'a',
 'cartoon',
 'comedy',
 'it',
 'ran',
 'at',
 'the',
 'same',
 'time',
 'as',
 'some',
 'other',
 'programs',
 'about',
 'school',
 'life',
 'such',
 'as',
 'teachers',
 'my',
 'years',
 'in',
 'the',
 'teaching',
 'profession',
 'lead',
 'me',
 'to',
 'believe',
 'that',
 'bromwell',
 'high',
 's',
 'satire',
 'is',
 'much',
 'closer',
 'to',
 'reality',
 'than',
 'is',
 'teachers',
 'the',
 'scramble',
 'to',
 'survive',
 'financially',
 'the',
 'insightful',
 'students',
 'who',
 'can',
 'see',
 'right',
 'through',
 'their',
 'pathetic',
 'teachers',
 'pomp',
 'the',
 'pettiness',
 'of',
 'the',
 'whole',
 'situation',
 'all',
 'remind',
 'me',
 'of',
 'the',
 'schools',
 'i',
 'knew',
 'and',
 'their',
 'students',
 'when',
 'i',
 'saw',
 'the',
 'episode',
 'in',
 'which',
 'a',
 'student',
 'repeatedly',
 'tried',
 'to',
 'burn',
 'down',
 'the',
 'school',
 'i',
 'immediately',
 'recalled',
 'at',
 'high',
 'a',
 'classic',
 'line',
 'inspecto

In [39]:
for a,b in Counter(words).items():
    if(b==0):
        print(a)

**Test your code**

As a text that you've implemented the dictionary correctly, print out the number of unique words in your vocabulary and the contents of the first, tokenized review.

In [40]:
# stats about vocabulary
print('Unique words: ', len((vocab_to_int)))  # should ~ 74000+
print()

# print tokens in first review
print('Tokenized review: \n', reviews_ints[:1])

Unique words:  74072

Tokenized review: 
 [[21025, 308, 6, 3, 1050, 207, 8, 2138, 32, 1, 171, 57, 15, 49, 81, 5785, 44, 382, 110, 140, 15, 5194, 60, 154, 9, 1, 4975, 5852, 475, 71, 5, 260, 12, 21025, 308, 13, 1978, 6, 74, 2395, 5, 613, 73, 6, 5194, 1, 24103, 5, 1983, 10166, 1, 5786, 1499, 36, 51, 66, 204, 145, 67, 1199, 5194, 19869, 1, 37442, 4, 1, 221, 883, 31, 2988, 71, 4, 1, 5787, 10, 686, 2, 67, 1499, 54, 10, 216, 1, 383, 9, 62, 3, 1406, 3686, 783, 5, 3483, 180, 1, 382, 10, 1212, 13583, 32, 308, 3, 349, 341, 2913, 10, 143, 127, 5, 7690, 30, 4, 129, 5194, 1406, 2326, 5, 21025, 308, 10, 528, 12, 109, 1448, 4, 60, 543, 102, 12, 21025, 308, 6, 227, 4146, 48, 3, 2211, 12, 8, 215, 23]]


#### Encoding the labels

Our labels are "positive" or "negative". To use these labels in our network, we need to convert them to 0 and 1.

> **Exercise:** Convert labels from `positive` and `negative` to 1 and 0, respectively, and place those in a new list, `encoded_labels`.

In [41]:
# 1=positive, 0=negative label conversion
encoded_labels = np.array([1 if label =='positive' else 0 for label in labels.split('\n')])

### Removing Outliers

As an additional pre-processing step, we want to make sure that our reviews are in good shape for standard processing. That is, our network will expect a standard input text size, and so, we'll want to shape our reviews into a specific length. We'll approach this task in two main steps:

1. Getting rid of extremely long or short reviews; the outliers
2. Padding/truncating the remaining data so that we have reviews of the same length.

<img src="assets/outliers_padding_ex.png" width=40%>

Before we pad our review text, we should check for reviews of extremely short or long lengths; outliers that may mess with our training.

In [27]:
encoded_labels

array([1, 0, 1, ..., 1, 0, 0])

In [42]:
# outlier review stats
review_lens = Counter([len(x) for x in reviews_ints])
print("Zero-length reviews: {}".format(review_lens[0]))
print("Maximum review length: {}".format(max(review_lens)))

Zero-length reviews: 1
Maximum review length: 2514


In [45]:
max(review_lens)

2514

Okay, a couple issues here. We seem to have one review with zero length. And, the maximum review length is way too many steps for our RNN. We'll have to remove any super short reviews and truncate super long reviews. This removes outliers and should allow our model to train more efficiently.

> **Exercise:** First, remove *any* reviews with zero length from the `reviews_ints` list and their corresponding label in `encoded_labels`.

In [60]:
print('Number of reviews before removing outliers: ', len(reviews_ints))

## remove any reviews/labels with zero length from the reviews_ints list.
non_zero_idx = [i for i, review_ints in enumerate(reviews_ints) if len(review_ints)>0 ]
reviews_ints = [reviews_ints[i] for i in non_zero_idx]
encoded_labels = np.array([encoded_labels[i] for i in non_zero_idx])

print('Number of reviews after removing outliers: ', len(reviews_ints))

Number of reviews before removing outliers:  25000
Number of reviews after removing outliers:  25000


---
## Padding sequences

To deal with both short and very long reviews, we'll pad or truncate all our reviews to a specific length. For reviews shorter than some `seq_length`, we'll pad with 0s. For reviews longer than `seq_length`, we can truncate them to the first `seq_length` words. A good `seq_length`, in this case, is 200.

> **Exercise:** Define a function that returns an array `features` that contains the padded data, of a standard size, that we'll pass to the network. 
* The data should come from `review_ints`, since we want to feed integers to the network. 
* Each row should be `seq_length` elements long. 
* For reviews shorter than `seq_length` words, **left pad** with 0s. That is, if the review is `['best', 'movie', 'ever']`, `[117, 18, 128]` as integers, the row will look like `[0, 0, 0, ..., 0, 117, 18, 128]`. 
* For reviews longer than `seq_length`, use only the first `seq_length` words as the feature vector.

As a small example, if the `seq_length=10` and an input review is: 
```
[117, 18, 128]
```
The resultant, padded sequence should be: 

```
[0, 0, 0, 0, 0, 0, 0, 117, 18, 128]
```

**Your final `features` array should be a 2D array, with as many rows as there are reviews, and as many columns as the specified `seq_length`.**

This isn't trivial and there are a bunch of ways to do this. But, if you're going to be building your own deep learning networks, you're going to have to get used to preparing your data.

In [159]:
def pad_features(reviews_ints, seq_length):
    ''' Return features of review_ints, where each review is padded with 0's 
        or truncated to the input seq_length.
    '''
    ## implement function
    features = np.zeros((len(reviews_ints), seq_length), dtype=int)

    # for each review, I grab that review and 
    print(reviews_ints)
    for i, row in enumerate(reviews_ints):
        features[i, -len(row):] = np.array(row)[:seq_length]
    
    return features

In [145]:
# Test your implementation!

seq_length = 200

features = pad_features(reviews_ints, seq_length=seq_length)

## test statements - do not change - ##
assert len(features)==len(reviews_ints), "Your features should have as many rows as reviews."
assert len(features[0])==seq_length, "Each feature row should contain seq_length values."

# print first 10 values of the first 30 batches 
print(features[:30,:10])

0
[21025, 308, 6, 3, 1050, 207, 8, 2138, 32, 1, 171, 57, 15, 49, 81, 5785, 44, 382, 110, 140, 15, 5194, 60, 154, 9, 1, 4975, 5852, 475, 71, 5, 260, 12, 21025, 308, 13, 1978, 6, 74, 2395, 5, 613, 73, 6, 5194, 1, 24103, 5, 1983, 10166, 1, 5786, 1499, 36, 51, 66, 204, 145, 67, 1199, 5194, 19869, 1, 37442, 4, 1, 221, 883, 31, 2988, 71, 4, 1, 5787, 10, 686, 2, 67, 1499, 54, 10, 216, 1, 383, 9, 62, 3, 1406, 3686, 783, 5, 3483, 180, 1, 382, 10, 1212, 13583, 32, 308, 3, 349, 341, 2913, 10, 143, 127, 5, 7690, 30, 4, 129, 5194, 1406, 2326, 5, 21025, 308, 10, 528, 12, 109, 1448, 4, 60, 543, 102, 12, 21025, 308, 6, 227, 4146, 48, 3, 2211, 12, 8, 215, 23]
1
[63, 4, 3, 125, 36, 47, 7472, 1395, 16, 3, 4181, 505, 45, 17, 3, 622, 134, 12, 6, 3, 1279, 457, 4, 1721, 207, 3, 10624, 7373, 300, 6, 667, 83, 35, 2116, 1086, 2989, 34, 1, 898, 46417, 4, 8, 13, 5096, 464, 8, 2656, 1721, 1, 221, 57, 17, 58, 794, 1297, 832, 228, 8, 43, 98, 123, 1469, 59, 147, 38, 1, 963, 142, 29, 667, 123, 1, 13584, 410, 61, 94, 1

722
[10, 14, 820, 56, 22, 3320, 3456, 2, 14, 18095, 34, 1, 1369, 333, 15, 3, 471, 19, 59, 93, 15, 149, 10, 254, 8, 1543, 440, 10, 28, 91, 3334, 359, 2, 6234, 105, 11, 20, 2, 28, 77, 90, 5174, 34, 1, 7432, 4, 3360, 2453, 33, 655, 102, 10, 143, 1006, 19, 40, 21, 26, 10, 89, 23, 122, 48, 8, 6, 44, 1, 3320, 19, 25, 208, 211, 1, 513, 47, 5, 29, 1, 2075, 341, 54, 21, 167, 32, 27, 604, 1080, 4, 332, 11, 20, 6, 3, 349, 2810, 22, 31, 1, 1133, 575, 496, 2, 14, 95, 160, 8, 13, 57, 8, 6, 24, 5, 29, 614, 601, 829, 119, 5006, 1681, 2654, 15243, 6, 3, 515, 8, 6, 2374, 12, 11, 20, 1463, 23, 77, 616, 22, 276, 9, 1, 2210, 10, 89, 23, 102, 8, 142, 29, 5589, 2, 47239, 39, 10, 301, 8, 13, 3, 349, 8, 554, 29, 220, 205, 2654, 39, 1, 1083, 289, 205, 2342, 13, 2, 466, 2425, 10, 200, 8]
723
[11, 196, 43, 211, 429, 2, 429, 844, 391, 2, 43, 1021, 24, 164, 1, 846, 6, 319, 19, 1, 533, 13, 15839, 3118, 145, 34, 264, 37, 250, 5, 7336, 58, 30, 33, 130, 56, 3475, 295, 149, 83, 1, 330, 784, 1, 1645, 177, 28, 2208, 9226,

1168
[862, 6, 9, 1, 922, 2, 115, 6, 9, 6043, 9, 6301, 963, 1727, 9, 11, 624, 2257, 63, 265, 427, 3, 875, 9, 3, 57, 9, 62, 7040, 70, 131, 9, 12544, 1, 1785, 70, 1196, 2, 4516, 2, 1, 6488, 6534, 2442, 444, 22, 1, 640, 34, 901, 4736, 2, 391, 16, 1, 261, 2, 516, 34, 1689, 18100, 374, 1, 1299, 6965, 4495, 9, 1, 421, 214, 3, 524, 11566, 26623, 2442, 302, 85, 2996, 9, 1, 711, 4121, 4, 389, 17398, 2, 2901, 5, 2120, 56, 147, 53, 749, 26, 3924, 5, 30, 159, 571, 123, 3, 1088, 9349, 12, 1034, 9, 1322, 53, 370, 715, 41, 7216, 22, 1517, 3, 3622, 16, 41, 441, 6351, 6202, 6528, 19, 1, 3714, 4, 41, 2375, 578, 1511, 5, 29, 325, 73, 2315, 2063, 41, 15756, 26, 10031, 34, 34, 1, 2228, 437, 5841, 3304, 7056, 615, 6031, 83, 2258, 4, 1, 468, 395, 306, 5, 29, 3, 223, 52, 10683, 73, 2442, 13, 2, 6206, 49, 871, 2944, 5, 1, 3883, 2, 2442, 37, 1930, 17, 48, 6, 204, 16, 400, 19114, 1, 468, 12, 6, 165, 1, 90, 660, 4, 31, 41, 203, 1, 176, 266, 2102, 2, 115, 19115, 19, 2442, 6, 44, 5, 698, 1, 2034, 3440, 16, 41, 189, 

1749
[2, 10, 377, 3249, 624, 11, 20, 920, 674, 1436, 374, 44, 287, 2, 3, 317, 623, 2, 163, 705, 12, 7, 7, 40, 65, 215, 23, 98, 74, 5, 133, 44, 11, 4212, 81, 73, 12, 256, 8, 47, 3, 368, 4, 65, 50, 1788, 90, 4, 8, 215, 23, 55, 164, 867, 126, 8, 158, 32, 31, 15, 3, 862, 87, 44, 15, 3, 711, 207, 24, 22, 129, 110, 90, 4, 1, 410, 6, 95, 98, 1010, 5, 29, 3453, 74, 325, 1117, 7, 7, 48, 13, 65, 32522, 6, 1, 846, 6, 24, 76, 32, 31, 11, 18, 97, 28, 77, 37, 74, 52, 257, 17, 31, 1, 1112, 1122, 22, 49, 4, 1, 5894, 753, 9, 62, 107, 26, 6378, 586, 17, 4909, 4332, 38, 1384, 1, 20, 13305, 1, 2556, 21490, 3597, 4, 1, 3491, 33111, 147, 31, 6867, 1514, 10539, 16, 11545, 36, 217, 208, 882, 324, 837, 19, 303, 4, 5798, 48, 142, 28, 77, 3, 48279, 4, 623, 8, 29499, 31, 4, 44, 287, 229, 5, 11, 3597, 2, 1076, 22, 9, 4844, 4, 1, 20, 13, 816, 862, 7, 7, 1, 171, 17, 3220, 8582, 1360, 104, 1, 33112, 524, 3981, 18, 318, 8582, 1360, 126, 3, 50, 289, 17, 48, 53, 13, 344, 19, 53, 13, 344, 2172, 163, 8, 13, 31, 24656, 255

2335
[388, 356, 4, 134, 1891, 31, 2348, 6, 407, 343, 34, 367, 7009, 42, 12047, 451, 12, 7493, 2311, 33344, 77, 3, 3979, 3103, 82, 30, 4, 1, 247, 472, 4086, 10, 139, 124, 548, 8404, 621, 7431, 45, 34, 224, 2, 118, 222, 33, 75, 67, 4093, 12, 1555, 268, 39, 3, 5113, 18319, 10, 120, 128, 315, 298, 22, 4515, 32, 1, 543, 4, 7, 7, 10, 222, 380, 100, 20, 1406, 142, 105, 11, 494, 229, 32, 3, 57, 37, 15, 5, 834, 87, 24, 5, 2219, 3, 20, 42, 14, 8, 1, 11132, 2129, 7, 7, 8, 13, 65, 98, 76, 86, 1, 2645, 14, 165, 3, 50, 1094, 43, 844, 2118, 31, 1, 95, 186, 786, 19272, 21, 142, 28, 1396, 3, 3331, 1379, 21, 155, 98, 50, 35, 270, 16, 140, 3, 7100, 2155]
2336
[13450, 6, 35, 457, 4, 87, 3, 187, 20, 51, 29, 1109, 17, 163, 52, 73, 3, 72, 2118, 112, 2, 3, 175, 4, 468, 92, 177, 151, 23, 28, 3845, 1409, 8, 151, 23, 28, 3, 192, 347, 2, 8, 430, 1485, 9, 1, 1087, 298, 1226, 19, 8, 20411, 31, 12, 17, 35, 1069, 2, 72, 391, 226, 35, 1109, 177, 2, 1, 1728, 4, 3, 157, 2427, 52, 22, 964, 1, 63, 73, 9, 4477, 693, 3448, 

...

17188
[15, 37, 109, 400, 28, 391, 11, 6, 3, 384, 644, 127, 6, 3, 999, 4, 1, 8988, 16, 251, 910, 3, 162, 2235, 3566, 320, 4535, 199, 2178, 719, 199, 4628, 572, 199, 199, 65596, 4628, 8113, 21254, 1794, 22, 258, 95, 2894, 2053, 2338, 2353, 22703, 4628, 13759, 65597, 737, 318, 1, 3728, 3477, 15787, 9012, 2235, 4535, 1183, 153, 5529, 92, 3, 1299, 245, 5294, 34273, 339, 7726, 3114, 982, 1, 15874, 2235, 1953, 4628, 6566, 9996, 8752, 65598, 6566, 4209, 15814, 5328, 2235, 13759, 199, 1794, 5879, 13759, 6938, 1, 2155, 13759, 4535, 23963]
17189
[46, 40, 13, 30, 152, 21, 51, 1535, 22, 809, 5, 80, 8, 13, 67, 7154, 1230, 5, 191, 3, 63, 2, 369, 8, 173, 2, 173, 2, 173, 59, 148, 1, 2136, 16, 721, 2, 1, 8266, 1512, 14, 3, 517, 573, 809, 13, 169, 5, 2428, 30, 4, 67, 90, 1167, 2179, 124, 8, 59, 68, 12, 6492, 11714, 134, 8, 13, 77, 220, 160, 2, 12, 13, 48, 10, 133, 5, 11, 786, 1482, 5, 366, 1, 432, 1094, 142, 29, 4001, 283, 6, 43, 3, 7209, 4, 1, 201, 18, 2, 59, 447, 4, 13554, 13, 65, 76, 99, 1, 8648, 2, 1

17665
[10, 474, 10, 14, 3602, 5, 11, 20, 197, 86, 4, 1, 472, 4, 1, 63, 2, 1, 952, 270, 37, 10, 509, 8, 3, 564, 38, 157, 31286, 5717, 5009, 1307, 677, 2669, 1289, 7148, 8633, 6, 265, 56, 34, 1, 555, 257, 21715, 4603, 9257, 8162, 3268, 25, 6, 894, 5, 138, 22, 1, 506, 12280, 3, 1308, 2, 138, 427, 96, 5, 774, 27, 203, 2, 27, 212, 13, 1409, 12, 13, 65, 31, 10, 51, 133, 44, 1, 63, 15, 10, 285, 23, 2636, 1, 16100, 678, 5, 29, 1178, 82, 1163, 8441, 6043, 15, 2194, 9489, 15055, 12840, 15, 2596, 2972, 5308, 66233, 15, 1969, 1289, 2933, 66234, 15, 1171, 4139, 5045, 31116, 15, 7370, 66235, 29158, 66236, 15, 15736, 26349, 9718, 22340, 15, 1748, 1289, 3618, 16004, 15, 1626, 1289, 2, 2579, 15002, 15, 2613, 1002, 8633, 166, 3, 183, 50, 235, 16, 48, 8, 13, 288, 2, 1, 20, 126, 28, 8, 13, 718, 4551, 381, 561, 17, 3, 1030, 965, 926, 1, 130, 19, 10, 51, 23, 133, 10, 499, 8, 15, 10, 161, 23, 167, 32, 8, 31, 845]
17666
[1, 2867, 14102, 186, 3, 237, 36, 206, 834, 5, 29, 1875, 16, 41, 203, 1698, 15, 53, 68, 1,

18169
[256, 10, 1124, 11, 18, 3, 16, 782, 3, 586, 574, 4, 765, 9, 264, 5, 968, 3, 480, 187, 20, 8, 14, 3, 22, 1, 3988, 164, 2371, 10, 422, 23, 803, 45, 48, 14, 169, 22, 9, 1, 18, 42, 36, 1, 78, 70, 19, 10, 161, 23, 452, 86, 10, 686, 174, 134, 14, 169, 5, 28, 141, 5, 94, 71, 1382, 17, 2112, 410, 6, 3, 4873, 461, 1, 18, 19, 10, 260, 11, 6, 86, 33, 636, 1404, 205, 3, 226, 1, 190, 12, 40, 6, 58, 112, 341, 166, 1, 18, 565, 9001, 8, 151, 23, 541, 46, 21, 848, 180, 2, 105, 1, 18, 38, 449, 5, 130, 42, 46, 21, 105, 8, 9, 9729, 21, 79, 29, 1443, 17, 3101, 10, 561, 39, 1, 134, 9, 62, 1, 6592, 26, 643, 497, 608, 186, 986, 3301, 253, 81, 17, 3752, 10, 260, 1, 947, 6095, 5, 11, 15, 2169, 1235]
18170
[1, 3201, 73, 110, 2547, 4, 11620, 11109, 2, 2842, 6119, 2, 1, 66767, 4, 706, 5957, 13575, 2, 1238, 4294, 26983, 119, 157, 1963, 3577, 13, 6081, 440, 84, 984, 17, 566, 1201, 256, 1201, 13, 2644, 5, 8006, 27, 314, 13, 568, 6, 1, 4063, 63, 5783, 6, 65, 35, 3116, 412, 17, 1, 9539, 30, 9, 3, 3165, 36782, 254

18612
[11, 18, 19218, 17, 71, 22, 106, 2170, 15, 3, 518, 10, 14, 14842, 38, 1220, 2, 9122, 22, 8722, 9979, 9, 3, 657, 2026, 136, 10, 3930, 1, 9012, 2, 68, 2460, 62, 1036, 13316, 1858, 16, 457, 2199, 3, 27815, 1920, 30, 454, 307, 16, 1, 55, 84, 57, 2, 2931, 3, 110, 10, 114, 97, 28, 68, 9, 1220, 10, 1026, 60, 212, 2, 3738, 44, 96, 775, 6, 35, 153, 125, 615, 311, 2, 471, 28, 197, 1108, 2, 36, 450, 572, 9, 3, 385, 657, 2026, 15, 35, 153, 125, 36, 6, 149, 205, 3, 311, 615, 346, 28, 1827, 994, 2, 408, 227, 243, 9, 159, 13811, 10, 239, 173, 5984, 2585, 1, 405, 13, 417, 6, 3, 1704, 6899, 17, 55, 1006, 989, 4, 4478, 3, 471, 234, 3, 907, 5438, 47, 2038, 198, 153, 775, 24065, 2, 11, 184, 10545, 775, 266, 9, 1767, 4, 88, 2, 413, 10646, 88, 38, 55, 1006, 2, 1795, 2300, 32, 1, 130, 4, 1, 63, 40, 6, 85, 1054, 234, 675, 5, 49, 20508, 13426, 8, 185, 12, 1, 471, 6, 169, 5, 1563, 279, 36, 47, 1370, 3, 1684, 632, 17, 88]
18613
[10, 377, 10, 195, 10, 548, 11, 788, 9, 1, 18, 19, 8, 14, 37, 76, 2, 45, 4, 269

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Training, Validation, Test

With our data in nice shape, we'll split it into training, validation, and test sets.

> **Exercise:** Create the training, validation, and test sets. 
* You'll need to create sets for the features and the labels, `train_x` and `train_y`, for example. 
* Define a split fraction, `split_frac` as the fraction of data to **keep** in the training set. Usually this is set to 0.8 or 0.9. 
* Whatever data is left will be split in half to create the validation and *testing* data.

In [115]:
split_frac = 0.8

## split data into training, validation, and test data (features and labels, x and y)

split_idx = int(len(features)*split_frac)
train_x, remaining_x = features[:split_idx], features[split_idx:]
train_y, remaining_y = encoded_labels[:split_idx], encoded_labels[split_idx:]

test_idx = int(len(remaining_x)*0.5)
val_x, test_x = remaining_x[:test_idx], remaining_x[test_idx:]
val_y, test_y = remaining_y[:test_idx], remaining_y[test_idx:]

## print out the shapes of your resultant feature data
print("\t\t\tFeature Shapes:")
print("Train set: \t\t{}".format(train_x.shape), 
      "\nValidation set: \t{}".format(val_x.shape),
      "\nTest set: \t\t{}".format(test_x.shape))


			Feature Shapes:
Train set: 		(20000, 200) 
Validation set: 	(2500, 200) 
Test set: 		(2500, 200)


**Check your work**

With train, validation, and test fractions equal to 0.8, 0.1, 0.1, respectively, the final, feature data shapes should look like:
```
                    Feature Shapes:
Train set: 		 (20000, 200) 
Validation set: 	(2500, 200) 
Test set: 		  (2500, 200)
```

---
## DataLoaders and Batching

After creating training, test, and validation data, we can create DataLoaders for this data by following two steps:
1. Create a known format for accessing our data, using [TensorDataset](https://pytorch.org/docs/stable/data.html#) which takes in an input set of data and a target set of data with the same first dimension, and creates a dataset.
2. Create DataLoaders and batch our training, validation, and test Tensor datasets.

```
train_data = TensorDataset(torch.from_numpy(train_x), torch.from_numpy(train_y))
train_loader = DataLoader(train_data, batch_size=batch_size)
```

This is an alternative to creating a generator function for batching our data into full batches.

In [116]:
import torch
from torch.utils.data import TensorDataset, DataLoader

# create Tensor datasets
train_data = TensorDataset(torch.from_numpy(train_x), torch.from_numpy(train_y))
valid_data = TensorDataset(torch.from_numpy(val_x), torch.from_numpy(val_y))
test_data = TensorDataset(torch.from_numpy(test_x), torch.from_numpy(test_y))

# dataloaders
batch_size = 50

# make sure to SHUFFLE your data
train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size)
valid_loader = DataLoader(valid_data, shuffle=True, batch_size=batch_size)
test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size)

In [117]:
# obtain one batch of training data
dataiter = iter(train_loader)
sample_x, sample_y = dataiter.next()

print('Sample input size: ', sample_x.size()) # batch_size, seq_length
print('Sample input: \n', sample_x)
print()
print('Sample label size: ', sample_y.size()) # batch_size
print('Sample label: \n', sample_y)

Sample input size:  torch.Size([50, 200])
Sample input: 
 tensor([[    0,     0,     0,  ...,  1096,  4795,  3971],
        [   87,   109, 29226,  ...,    48,    10,   377],
        [    0,     0,     0,  ...,     2,  1510,  4851],
        ...,
        [   10,  2706,  6148,  ...,     1,   330,  1466],
        [  602,  1011,     7,  ...,   296,    41,    31],
        [   15,     3, 10102,  ..., 41348,     5,     1]])

Sample label size:  torch.Size([50])
Sample label: 
 tensor([0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1,
        0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0,
        1, 1])


---
# Sentiment Network with PyTorch

Below is where you'll define the network.

<img src="assets/network_diagram.png" width=40%>

The layers are as follows:
1. An [embedding layer](https://pytorch.org/docs/stable/nn.html#embedding) that converts our word tokens (integers) into embeddings of a specific size.
2. An [LSTM layer](https://pytorch.org/docs/stable/nn.html#lstm) defined by a hidden_state size and number of layers
3. A fully-connected output layer that maps the LSTM layer outputs to a desired output_size
4. A sigmoid activation layer which turns all outputs into a value 0-1; return **only the last sigmoid output** as the output of this network.

### The Embedding Layer

We need to add an [embedding layer](https://pytorch.org/docs/stable/nn.html#embedding) because there are 74000+ words in our vocabulary. It is massively inefficient to one-hot encode that many classes. So, instead of one-hot encoding, we can have an embedding layer and use that layer as a lookup table. You could train an embedding layer using Word2Vec, then load it here. But, it's fine to just make a new layer, using it for only dimensionality reduction, and let the network learn the weights.


### The LSTM Layer(s)

We'll create an [LSTM](https://pytorch.org/docs/stable/nn.html#lstm) to use in our recurrent network, which takes in an input_size, a hidden_dim, a number of layers, a dropout probability (for dropout between multiple layers), and a batch_first parameter.

Most of the time, you're network will have better performance with more layers; between 2-3. Adding more layers allows the network to learn really complex relationships. 

> **Exercise:** Complete the `__init__`, `forward`, and `init_hidden` functions for the SentimentRNN model class.

Note: `init_hidden` should initialize the hidden and cell state of an lstm layer to all zeros, and move those state to GPU, if available.

In [118]:
# First checking if GPU is available
train_on_gpu=torch.cuda.is_available()

if(train_on_gpu):
    print('Training on GPU.')
else:
    print('No GPU available, training on CPU.')

No GPU available, training on CPU.


In [125]:
import torch.nn as nn

class SentimentRNN(nn.Module):
    """
    The RNN model that will be used to perform Sentiment analysis.
    """

    def __init__(self, vocab_size, output_size, embedding_dim, hidden_dim, n_layers, drop_prob=0.5):
        """
        Initialize the model by setting up the layers.
        """
        super(SentimentRNN, self).__init__()

        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim
        
        # define all layers
        self.embed = nn.Embedding(vocab_size, embedding_dim)
        self.lstm= nn.LSTM(embedding_dim, hidden_dim, n_layers, dropout = drop_prob, batch_first = True )
        self.dropout= nn.Dropout(0.3)
        self.fc = nn.Linear(hidden_dim, output_size)
        self.sigmoid = nn.Sigmoid()

    def forward(self, x, hidden):
        """
        Perform a forward pass of our model on some input and hidden state.
        """
        batch_size = x.size(0)
        x = x.long()
        embedding = self.embed(x)
        lstm_out, hidden = self.lstm(embedding, hidden)
        lstm_out = lstm_out.contiguous().view(-1, self.hidden_dim)
        
        out = self.dropout(lstm_out)
        out_fc = self.fc(out)
        
        sig_out = self.sigmoid(out_fc)
        
        # reshape to be batch_size first
        sig_out = sig_out.view(batch_size, -1)
        sig_out = sig_out[:, -1] # get last batch of labels
        
        # return last sigmoid output and hidden state
        return sig_out, hidden
    
    
    def init_hidden(self, batch_size):
        ''' Initializes hidden state '''
        # Create two new tensors with sizes n_layers x batch_size x hidden_dim,
        # initialized to zero, for hidden state and cell state of LSTM
        weight = next(self.parameters()).data
        
        if (train_on_gpu):
            hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_().cuda(),
                  weight.new(self.n_layers, batch_size, self.hidden_dim).zero_().cuda())
        else:
            hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_(),
                      weight.new(self.n_layers, batch_size, self.hidden_dim).zero_())
        return hidden
        

## Instantiate the network

Here, we'll instantiate the network. First up, defining the hyperparameters.

* `vocab_size`: Size of our vocabulary or the range of values for our input, word tokens.
* `output_size`: Size of our desired output; the number of class scores we want to output (pos/neg).
* `embedding_dim`: Number of columns in the embedding lookup table; size of our embeddings.
* `hidden_dim`: Number of units in the hidden layers of our LSTM cells. Usually larger is better performance wise. Common values are 128, 256, 512, etc.
* `n_layers`: Number of LSTM layers in the network. Typically between 1-3

> **Exercise:** Define the model  hyperparameters.


In [126]:
# Instantiate the model w/ hyperparams
vocab_size = len(vocab_to_int) + 1
output_size = 1
embedding_dim = 400
hidden_dim = 256
n_layers = 2

net = SentimentRNN(vocab_size, output_size, embedding_dim, hidden_dim, n_layers)

print(net)

SentimentRNN(
  (embed): Embedding(74073, 400)
  (lstm): LSTM(400, 256, num_layers=2, batch_first=True, dropout=0.5)
  (dropout): Dropout(p=0.3)
  (fc): Linear(in_features=256, out_features=1, bias=True)
  (sigmoid): Sigmoid()
)


---
## Training

Below is the typical training code. If you want to do this yourself, feel free to delete all this code and implement it yourself. You can also add code to save a model by name.

>We'll also be using a new kind of cross entropy loss, which is designed to work with a single Sigmoid output. [BCELoss](https://pytorch.org/docs/stable/nn.html#bceloss), or **Binary Cross Entropy Loss**, applies cross entropy loss to a single value between 0 and 1.

We also have some data and training hyparameters:

* `lr`: Learning rate for our optimizer.
* `epochs`: Number of times to iterate through the training dataset.
* `clip`: The maximum gradient value to clip at (to prevent exploding gradients).

In [127]:
# loss and optimization functions
lr=0.001

criterion = nn.BCELoss()
optimizer = torch.optim.Adam(net.parameters(), lr=lr)


In [128]:
# training params

epochs = 4 # 3-4 is approx where I noticed the validation loss stop decreasing

counter = 0
print_every = 100
clip=5 # gradient clipping

# move model to GPU, if available
if(train_on_gpu):
    net.cuda()

net.train()
# train for some number of epochs
for e in range(epochs):
    # initialize hidden state
    h = net.init_hidden(batch_size)

    # batch loop
    for inputs, labels in train_loader:
        counter += 1

        if(train_on_gpu):
            inputs, labels = inputs.cuda(), labels.cuda()

        # Creating new variables for the hidden state, otherwise
        # we'd backprop through the entire training history
        h = tuple([each.data for each in h])

        # zero accumulated gradients
        net.zero_grad()

        # get the output from the model
        output, h = net(inputs, h)

        # calculate the loss and perform backprop
        loss = criterion(output.squeeze(), labels.float())
        loss.backward()
        # `clip_grad_norm` helps prevent the exploding gradient problem in RNNs / LSTMs.
        nn.utils.clip_grad_norm_(net.parameters(), clip)
        optimizer.step()

        # loss stats
        if counter % print_every == 0:
            # Get validation loss
            val_h = net.init_hidden(batch_size)
            val_losses = []
            net.eval()
            for inputs, labels in valid_loader:

                # Creating new variables for the hidden state, otherwise
                # we'd backprop through the entire training history
                val_h = tuple([each.data for each in val_h])

                if(train_on_gpu):
                    inputs, labels = inputs.cuda(), labels.cuda()

                output, val_h = net(inputs, val_h)
                val_loss = criterion(output.squeeze(), labels.float())

                val_losses.append(val_loss.item())

            net.train()
            print("Epoch: {}/{}...".format(e+1, epochs),
                  "Step: {}...".format(counter),
                  "Loss: {:.6f}...".format(loss.item()),
                  "Val Loss: {:.6f}".format(np.mean(val_losses)))

Epoch: 1/4... Step: 100... Loss: 0.687459... Val Loss: 0.687234


KeyboardInterrupt: 

---
## Testing

There are a few ways to test your network.

* **Test data performance:** First, we'll see how our trained model performs on all of our defined test_data, above. We'll calculate the average loss and accuracy over the test data.

* **Inference on user-generated data:** Second, we'll see if we can input just one example review at a time (without a label), and see what the trained model predicts. Looking at new, user input data like this, and predicting an output label, is called **inference**.

In [129]:
# Get test data loss and accuracy

test_losses = [] # track loss
num_correct = 0

# init hidden state
h = net.init_hidden(batch_size)

net.eval()
# iterate over test data
for inputs, labels in test_loader:

    # Creating new variables for the hidden state, otherwise
    # we'd backprop through the entire training history
    h = tuple([each.data for each in h])

    if(train_on_gpu):
        inputs, labels = inputs.cuda(), labels.cuda()
    
    # get predicted outputs
    output, h = net(inputs, h)
    
    # calculate loss
    test_loss = criterion(output.squeeze(), labels.float())
    test_losses.append(test_loss.item())
    
    # convert output probabilities to predicted class (0 or 1)
    pred = torch.round(output.squeeze())  # rounds to the nearest integer
    
    # compare predictions to true label
    correct_tensor = pred.eq(labels.float().view_as(pred))
    correct = np.squeeze(correct_tensor.numpy()) if not train_on_gpu else np.squeeze(correct_tensor.cpu().numpy())
    num_correct += np.sum(correct)


# -- stats! -- ##
# avg test loss
print("Test loss: {:.3f}".format(np.mean(test_losses)))

# accuracy over all test data
test_acc = num_correct/len(test_loader.dataset)
print("Test accuracy: {:.3f}".format(test_acc))

KeyboardInterrupt: 

### Inference on a test review

You can change this test_review to any text that you want. Read it and think: is it pos or neg? Then see if your model predicts correctly!
    
> **Exercise:** Write a `predict` function that takes in a trained net, a plain text_review, and a sequence length, and prints out a custom statement for a positive or negative review!
* You can use any functions that you've already defined or define any helper functions you want to complete `predict`, but it should just take in a trained net, a text review, and a sequence length.


In [133]:
# negative test review
test_review_neg = 'The worst movie I have seen; acting was terrible and I want my money back. This movie had bad acting and the dialogue was slow.'


In [151]:
def tokenize_review(test_review):
    review = test_review.lower() # lowercase, standardize
    all_text = ''.join([c for c in review if c not in punctuation])
    review_ints = []
    review_ints.append([vocab_to_int[word] for word in all_text.split()])
    return review_ints

test_ints = tokenize_review(test_review_neg)
print(test_ints)

[[1, 247, 18, 10, 28, 108, 113, 14, 388, 2, 10, 181, 60, 273, 144, 11, 18, 68, 76, 113, 2, 1, 410, 14, 539]]


In [154]:
# test sequence padding
seq_length=200
features = pad_features(test_ints, seq_length)

print(features)

[[1, 247, 18, 10, 28, 108, 113, 14, 388, 2, 10, 181, 60, 273, 144, 11, 18, 68, 76, 113, 2, 1, 410, 14, 539]]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   

In [155]:
len(test_ints)

1

In [160]:
def predict(net, test_review, sequence_length=200):
    ''' Prints out whether a give review is predicted to be 
        positive or negative in sentiment, using a trained model.
        
        params:
        net - A trained net 
        test_review - a review made of normal text and punctuation
        sequence_length - the padded length of a review
        '''
    # Convert test_review into int
    test_ints = tokenize_review(test_review)
    features = pad_features(test_ints, seq_length=seq_length)
    # convert to tensor to pass into your model
    feature_tensor = torch.from_numpy(features)
    batch_size = feature_tensor.size(0)
    h = net.init_hidden(batch_size)
    if(train_on_gpu):
        feature_tensor = feature_tensor.cuda()
    output, h = net(feature_tensor, h)
    # print custom response based on whether test_review is pos/neg
    # convert output probabilities to predicted class (0 or 1)
    pred = torch.round(output.squeeze()) 
    # printing output value, before rounding
    print('Prediction value, pre-rounding: {:.6f}'.format(output.item()))
    
    # print custom response
    if(pred.item()==1):
        print("Positive review detected!")
    else:
        print("Negative review detected.")
        

In [161]:
# positive test review
test_review_pos = 'This movie had the best acting and the dialogue was so good. I loved it.'


In [163]:
# call function
# try negative and positive reviews!
seq_length=200
predict(net, test_review_neg, seq_length)
predict(net, test_review_pos, seq_length)

[[1, 247, 18, 10, 28, 108, 113, 14, 388, 2, 10, 181, 60, 273, 144, 11, 18, 68, 76, 113, 2, 1, 410, 14, 539]]
Prediction value, pre-rounding: 0.236433
Negative review detected.
[[11, 18, 68, 1, 117, 113, 2, 1, 410, 14, 37, 50, 10, 445, 8]]
Prediction value, pre-rounding: 0.519246
Positive review detected!


### Try out test_reviews of your own!

Now that you have a trained model and a predict function, you can pass in _any_ kind of text and this model will predict whether the text has a positive or negative sentiment. Push this model to its limits and try to find what words it associates with positive or negative.

Later, you'll learn how to deploy a model like this to a production environment so that it can respond to any kind of user data put into a web app!